In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

        
# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/open-problems-multimodal/sample_submission.csv
/kaggle/input/open-problems-multimodal/train_cite_targets.h5
/kaggle/input/open-problems-multimodal/metadata_cite_day_2_donor_27678.csv
/kaggle/input/open-problems-multimodal/test_multi_inputs.h5
/kaggle/input/open-problems-multimodal/evaluation_ids.csv
/kaggle/input/open-problems-multimodal/train_cite_inputs.h5
/kaggle/input/open-problems-multimodal/train_multi_targets.h5
/kaggle/input/open-problems-multimodal/train_multi_inputs.h5
/kaggle/input/open-problems-multimodal/metadata.csv
/kaggle/input/open-problems-multimodal/test_cite_inputs_day_2_donor_27678.h5
/kaggle/input/open-problems-multimodal/test_cite_inputs.h5


In [2]:
import os, gc, pickle
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from colorama import Fore, Back, Style
from matplotlib.ticker import MaxNLocator
import warnings
warnings.simplefilter('ignore')
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler, scale
from sklearn.decomposition import PCA
from sklearn.dummy import DummyRegressor
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.multioutput import MultiOutputRegressor
import lightgbm as lgb
from sklearn.compose import TransformedTargetRegressor
from sklearn.metrics import mean_squared_error

DATA_DIR = "/kaggle/input/open-problems-multimodal/"
FP_CELL_METADATA = os.path.join(DATA_DIR,"metadata.csv")

FP_CITE_TRAIN_INPUTS = os.path.join(DATA_DIR,"train_cite_inputs.h5")
FP_CITE_TRAIN_TARGETS = os.path.join(DATA_DIR,"train_cite_targets.h5")
FP_CITE_TEST_INPUTS = os.path.join(DATA_DIR,"test_cite_inputs.h5")

FP_MULTIOME_TRAIN_INPUTS = os.path.join(DATA_DIR,"train_multi_inputs.h5")
FP_MULTIOME_TRAIN_TARGETS = os.path.join(DATA_DIR,"train_multi_targets.h5")
FP_MULTIOME_TEST_INPUTS = os.path.join(DATA_DIR,"test_multi_inputs.h5")

FP_SUBMISSION = os.path.join(DATA_DIR,"sample_submission.csv")
FP_EVALUATION_IDS = os.path.join(DATA_DIR,"evaluation_ids.csv")

In [3]:
!pip install --quiet tables

In [4]:
df_cell = pd.read_csv(FP_CELL_METADATA)
df_cell_cite = df_cell[df_cell.technology=="citeseq"]
df_cell_multi = df_cell[df_cell.technology=="multiome"]
df_cell_cite.shape, df_cell_multi.shape

((119651, 5), (161877, 5))

In [5]:
%%time
# Preprocessing
col_start = 10000

class PreprocessCiteseq(BaseEstimator, TransformerMixin):
    columns_to_use = 13000
    
    @staticmethod
    def take_column_subset(X):
        return X[:,-(PreprocessCiteseq.columns_to_use+col_start):-col_start]
    
    def transform(self, X):
        print(X.shape)
        X = X[:,~self.all_zero_columns]
        print(X.shape)
        X = PreprocessCiteseq.take_column_subset(X) # use only a part of the columns
        print(X.shape)
        gc.collect()

        X = self.pca.transform(X)
        print(X.shape)
        return X

    def fit_transform(self, X):
        gc.collect()
        print(X.shape)
        self.all_zero_columns = (X == 0).all(axis=0)
        X = X[:,~self.all_zero_columns]
        print(X.shape)
        X = PreprocessCiteseq.take_column_subset(X) # use only a part of the columns
        print(X.shape)
        gc.collect()

        self.pca = PCA(n_components=100, copy=False, random_state=1)
        X = self.pca.fit_transform(X)
#         plt.plot(self.pca.explained_variance_ratio_.cumsum())
#         plt.title("Cumulative explained variance ratio")
#         plt.gca().xaxis.set_major_locator(MaxNLocator(integer=True))
#         plt.xlabel('PCA component')
#         plt.ylabel('Cumulative explained variance ratio')
#         plt.show()
        print(X.shape)
        return X

preprocessor = PreprocessCiteseq()

cite_train_x = None
cite_train_x = preprocessor.fit_transform(pd.read_hdf(FP_CITE_TRAIN_INPUTS).values)

cite_train_y = pd.read_hdf(FP_CITE_TRAIN_TARGETS).values
print(cite_train_y.shape)

cite_test_x = preprocessor.fit_transform(pd.read_hdf(FP_CITE_TEST_INPUTS).values)
print(cite_test_x.shape)

(70988, 22050)
(70988, 21601)
(70988, 11601)
(70988, 100)
(70988, 140)
(48663, 22050)
(48663, 21305)
(48663, 11305)
(48663, 100)
(48663, 100)
CPU times: user 3min 24s, sys: 26.2 s, total: 3min 51s
Wall time: 2min 30s


In [6]:
pip install lightgbm xgboost catboost scikit-learn 

Note: you may need to restart the kernel to use updated packages.


In [7]:
from sklearn.metrics import r2_score

In [8]:
from catboost import CatBoostRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import r2_score, mean_squared_error
import gc

# Function to train and evaluate a model
def train_and_evaluate_model(model, train_x, train_y):
    model.fit(train_x, train_y)
    y_pred = model.predict(train_x)
    r2_scores = r2_score(train_y, y_pred, multioutput='raw_values')
    mse_scores = mean_squared_error(train_y, y_pred, multioutput='raw_values')
    r2_total = r2_score(train_y, y_pred)
    mse_total = mean_squared_error(train_y, y_pred)
    return r2_scores, r2_total, mse_scores, mse_total, model

# Define CatBoost parameters
params = {
    'iterations': 1000,             # equivalent to n_estimators
    'learning_rate': 0.1,
    'random_seed': 42,
    'l2_leaf_reg': 0.2,             # regularization parameter
    'depth': 10,                    # equivalent to max_depth
    'rsm': 0.8,                     # equivalent to colsample_bytree
    'subsample': 0.5,
    'min_data_in_leaf': 83,         # equivalent to min_child_samples
    'bagging_temperature': 1,       # bagging parameter
    'random_strength': 1,           # used to control the amount of randomness
    'one_hot_max_size': 2,          # for categorical features
    'leaf_estimation_method': 'Newton', # estimation method for leaf values
}
# Initialize CatBoost regressor
catboost_model = CatBoostRegressor(**params)

# Wrap CatBoost model in MultiOutputRegressor for multi-output support
multi_output_catboost = MultiOutputRegressor(catboost_model)

print('Training CatBoost model with MultiOutputRegressor...')
r2_scores, r2_total, mse_scores, mse_total, trained_model = train_and_evaluate_model(multi_output_catboost, cite_train_x, cite_train_y)

# Print R2 scores and MSE for each target
for i, r2 in enumerate(r2_scores):
    print(f'R^2 Score for Target {i}: {r2}')
    print(f'MSE for Target {i}: {mse_scores[i]}')

print('R^2 score total:', r2_total)
print('MSE total :', mse_total)

# Clean up to free memory
gc.collect()


Training CatBoost model with MultiOutputRegressor...
0:	learn: 1.3754098	total: 192ms	remaining: 3m 11s
1:	learn: 1.3587290	total: 325ms	remaining: 2m 42s
2:	learn: 1.3439797	total: 461ms	remaining: 2m 33s
3:	learn: 1.3324558	total: 598ms	remaining: 2m 28s
4:	learn: 1.3217244	total: 736ms	remaining: 2m 26s
5:	learn: 1.3111931	total: 876ms	remaining: 2m 25s
6:	learn: 1.2999593	total: 1.01s	remaining: 2m 22s
7:	learn: 1.2899973	total: 1.15s	remaining: 2m 22s
8:	learn: 1.2821491	total: 1.31s	remaining: 2m 23s
9:	learn: 1.2759278	total: 1.45s	remaining: 2m 23s
10:	learn: 1.2687322	total: 1.58s	remaining: 2m 22s
11:	learn: 1.2626984	total: 1.72s	remaining: 2m 21s
12:	learn: 1.2570864	total: 1.86s	remaining: 2m 21s
13:	learn: 1.2522432	total: 1.99s	remaining: 2m 20s
14:	learn: 1.2472441	total: 2.12s	remaining: 2m 19s
15:	learn: 1.2428637	total: 2.26s	remaining: 2m 18s
16:	learn: 1.2385784	total: 2.4s	remaining: 2m 18s
17:	learn: 1.2339255	total: 2.53s	remaining: 2m 18s
18:	learn: 1.2291918	t

54

In [9]:
print("Hello World")

Hello World
